# Load data 


The goal of this notebook is to move a collection of paired input and target images ready to be used for training and inference via the Pix2PixHD GAN model. The core functions used within this notebook are the train_test_move_commands2 which generates the slurm command to move each image accordingly.</br>

Please see the Pix2PixHD readme for the full requirements on how to set the data loaders but in short the files path must be as follows: </br>

**Train:**

   **/path/to/files/train_A** </br>
   
   **/path/to/files/train_B**
   
**Val:**

   **/path/to/files/val_A**   
   
   **/path/to/files/val_B**

**Test:**

   **/path/to/files/test_A**   
   
   **/path/to/files/test_B** </br>
   
### <span style ='color:red'>IMPORTANT!
   
The files are saved ***BARCODE_rXXcXXfXXp01.tiff*** for example 3CG0021772_r01c01f02p01.tiff. This is to ensure that files from different barcodes do not overwright other files. Following this is very important for downstream implementation. </br>

I have chosen to combine the image paths along with all the meta data into a CSV and extract random samples based on my experiment design. The dataset  but you can follow any approach you wish as long as you save the images in the format outlined above.
    



### Import paramters and helper functions

In [1]:
import os
import shutil
import sys
import numpy as np
import pandas as pd
root_dir = '../../../'
sys.path.append(root_dir)

from slurm.sbatch import submit_array
from slurm.commands import move_16bitimage
from slurm.commands import combine_AB
from utils.df_utils  import df_channel_create as channel_create
from utils.df_utils import df_image_folder_match as image_folder_match
from utils.util_utils import extract_samples, find_file, train_test_move_commands2,create_directory



### Define paths

**You will need to as a MINIMUM UPDATE**:
- conda_path
- repo_path
- model_name
- tissue: either Lung, Breast or Ovarian
- output_path: where to save images


In [2]:
## Mandatory to update
conda_path = os.path.join(
    '/hpc/projects/upt/bioimaging_analytics/Tesaro-DNA-Damage/conda_envs/',
    'pytorch_cyclegan'
)

repo_path = os.path.join(
    '/hpc/scratch/nvme3/smt29021/phase1_repo_1122/Structure-Specific-Contrast-Enhancement/workflow/phase2_sampling_normalisation/',
)

model_name = "bf_fitc_30k_nontoxic"
tissue = "Lung"

output_path = os.path.join(
    "/hpc/scratch/hdd3/smt29021/Tesaro-DNA-Damage/Data/",
#     "APPROACH_Pix2PixHD", 
    tissue, "Step1_Preprocessing/ACT1_Normalise",
    model_name
)

# toxicity_layout = os.path.join('/hpc/scratch/rdip1/smt29021/Tesaro-DNA-Damage/Data/APPROACH_Pix2PixHD/Lung/Step1_Preprocessing/ACT3_Evaluate/dataset_sizes_test/bf_dna_16bit_lung_val2_7000imgs/error_analysis/lung_val_plate_setting_toxicity.csv')


## Non-mandatory to update
py_path = os.path.join(repo_path,
                       'move_tesaro.py'
)

random_val_samples_path = os.path.join(
    "/hpc/scratch/rdip1/smt29021/Tesaro-DNA-Damage/Data/DATA_Processing/"
)

good_lung_val_csv_path = os.path.join(
"/hpc/projects/upt/bioimaging_analytics/Tesaro-DNA-Damage/error_analysis/br_val_good_bf.csv"
)


### Load Tesaro CSV

In [3]:
#Import Good Lung Images
img_data = pd.read_csv(good_lung_val_csv_path)
print("Number of Images: "+str(img_data.shape[0]))
img_data.head()

Number of Images: 159264


Unnamed: 0  Unnamed: 0.1  Unnamed: 0.1.1  \
0           1             1               1   
1           5             5               5   
2           9             9               9   
3          13            13              13   
4          17            17              17   

                                           image_url  \
0  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   
1  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   
2  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   
3  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   
4  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   

                                            new_path  \
0  3CG0019090_r01c01f01p01.tiffTesaro-DNA-Damage-...   
1  3CG0019090_r01c01f02p01.tiffTesaro-DNA-Damage-...   
2  3CG0019090_r01c01f03p01.tiffTesaro-DNA-Damage-...   
3  3CG0019090_r01c01f04p01.tiffTesaro-DNA-Damage-...   
4  3CG0019090_r01c01f05p01.tiffTesaro-DNA-Damage-...   

                                             new_loc  \
0  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   
1  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   
2  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   
3  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   
4  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   

                            URL_x  Row  Col  FieldID  ...  \
0  r01c01f01p01-ch2sk1fk1fl1.tiff    1    1        1  ...   
1  r01c01f02p01-ch2sk1fk1fl1.tiff    1    1        2  ...   
2  r01c01f03p01-ch2sk1fk1fl1.tiff    1    1        3  ...   
3  r01c01f04p01-ch2sk1fk1fl1.tiff    1    1        4  ...   
4  r01c01f05p01-ch2sk1fk1fl1.tiff    1    1        5  ...   

   ObjectiveMagnification                                       ExposureTime  \
0                      20  [[0.987330,0,0,-11.9],[0,-0.987330,0,1.4],[0,0...   
1                      20  [[0.987330,0,0,-11.9],[0,-0.987330,0,1.4],[0,0...   
2                      20  [[0.987330,0,0,-11.9],[0,-0.987330,0,1.4],[0,0...   
3                      20  [[0.987330,0,0,-11.9],[0,-0.987330,0,1.4],[0,0...   
4                      20  [[0.987330,0,0,-11.9],[0,-0.987330,0,1.4],[0,0...   

                       image_folder1 final_cell_line tissue_final  \
0  ELN15196_Br_DNA_Damage_Val_072220      3CG0019090       Breast   
1  ELN15196_Br_DNA_Damage_Val_072220      3CG0019090       Breast   
2  ELN15196_Br_DNA_Damage_Val_072220      3CG0019090       Breast   
3  ELN15196_Br_DNA_Damage_Val_072220      3CG0019090       Breast   
4  ELN15196_Br_DNA_Damage_Val_072220      3CG0019090       Breast   

                                    UID  plate_setting  \
0  0f153a11-a6a5-4314-83ee-64717436b270            Val   
1  9789fe3b-dd96-4baf-b5eb-dfe077b5947d            Val   
2  b75e3e1d-8760-44c9-88a3-b9417e1da384            Val   
3  286f6190-b279-4855-99d2-630d89e1b9f2            Val   
4  a2afa1a1-60ef-425e-b97a-1fdecbdb001d            Val   

                                         key                     key_final  \
0  3CG0019090_r01c01f01p01-ch2sk1fk1fl1.tiff  3CG0019090_r01c01f01p01.tiff   
1  3CG0019090_r01c01f02p01-ch2sk1fk1fl1.tiff  3CG0019090_r01c01f02p01.tiff   
2  3CG0019090_r01c01f03p01-ch2sk1fk1fl1.tiff  3CG0019090_r01c01f03p01.tiff   
3  3CG0019090_r01c01f04p01-ch2sk1fk1fl1.tiff  3CG0019090_r01c01f04p01.tiff   
4  3CG0019090_r01c01f05p01-ch2sk1fk1fl1.tiff  3CG0019090_r01c01f05p01.tiff   

   toxic  
0      1  
1      1  
2      1  
3      1  
4      1  

[5 rows x 34 columns]

### Load txt file containing row index of chosen Bright-field samples and then generate the corresponding target paths

In [6]:
test_plates_ov = ['3CG0022742','3CG0022796','3CG0022700']
test_plates_lu  = ['3CG0021760','3CG0021816','3CG0021766']
test_plates_br  = ['3CG0019162','3CG0019164','3CG0019156']

img_data = img_data[img_data["ChannelName"] == "Brightfield"]

breast_plates = img_data[~img_data['final_cell_line'].isin(test_plates_br)]
breast_plates_toxic = breast_plates[breast_plates['toxic'] ==1]
breast_plates_nontoxic = breast_plates[breast_plates['toxic'] ==0]
print(f"Total Toxic {breast_plates_toxic['toxic'].sum()}")
print(f"Total Non-Toxic {breast_plates_nontoxic['toxic'].count()}")

Total Toxic 49901
Total Non-Toxic 99000


In [7]:
'/hpc/scratch/rdip1/smt29021/Tesaro-DNA-Damage/Data/DATA_Processing/'
#Generate bf samples
indexes, lung_val_30000_bf = extract_samples(
    "br_val_nontoxicsamples_30000.txt",breast_plates_nontoxic,random_val_samples_path)

#Generate target channels and inputs for move
lung_val_sig = image_folder_match(img_data,lung_val_30000_bf,"image_url","Brightfield")
print(lung_val_sig.shape)
lung_val_sig.head()

(30000, 34)


Unnamed: 0  Unnamed: 0.1  Unnamed: 0.1.1  \
27         109           109             109   
31         125           125             125   
32         129           129             129   
34         137           137             137   
36         145           145             145   

                                            image_url  \
27  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   
31  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   
32  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   
34  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   
36  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   

                                             new_path  \
27  3CG0019090_r01c04f01p01.tiffTesaro-DNA-Damage-...   
31  3CG0019090_r01c04f05p01.tiffTesaro-DNA-Damage-...   
32  3CG0019090_r01c04f06p01.tiffTesaro-DNA-Damage-...   
34  3CG0019090_r01c04f08p01.tiffTesaro-DNA-Damage-...   
36  3CG0019090_r01c05f01p01.tiffTesaro-DNA-Damage-...   

                                              new_loc  \
27  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   
31  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   
32  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   
34  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   
36  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   

                             URL_x  Row  Col  FieldID  ...  \
27  r01c04f01p01-ch2sk1fk1fl1.tiff    1    4        1  ...   
31  r01c04f05p01-ch2sk1fk1fl1.tiff    1    4        5  ...   
32  r01c04f06p01-ch2sk1fk1fl1.tiff    1    4        6  ...   
34  r01c04f08p01-ch2sk1fk1fl1.tiff    1    4        8  ...   
36  r01c05f01p01-ch2sk1fk1fl1.tiff    1    5        1  ...   

    ObjectiveMagnification                                       ExposureTime  \
27                      20  [[0.987330,0,0,-11.9],[0,-0.987330,0,1.4],[0,0...   
31                      20  [[0.987330,0,0,-11.9],[0,-0.987330,0,1.4],[0,0...   
32                      20  [[0.987330,0,0,-11.9],[0,-0.987330,0,1.4],[0,0...   
34                      20  [[0.987330,0,0,-11.9],[0,-0.987330,0,1.4],[0,0...   
36                      20  [[0.987330,0,0,-11.9],[0,-0.987330,0,1.4],[0,0...   

                        image_folder1 final_cell_line tissue_final  \
27  ELN15196_Br_DNA_Damage_Val_072220      3CG0019090       Breast   
31  ELN15196_Br_DNA_Damage_Val_072220      3CG0019090       Breast   
32  ELN15196_Br_DNA_Damage_Val_072220      3CG0019090       Breast   
34  ELN15196_Br_DNA_Damage_Val_072220      3CG0019090       Breast   
36  ELN15196_Br_DNA_Damage_Val_072220      3CG0019090       Breast   

                                     UID  plate_setting  \
27  7c68fdff-0f79-424a-8d48-531e9671998b            Val   
31  977d2f1f-ddfd-43cb-87d3-4721b9675289            Val   
32  6de85e67-30d0-4b03-94ef-09da183b2e70            Val   
34  91db6d72-6d48-4384-957a-4654815a757c            Val   
36  9b18a222-f8ff-4301-b37b-89ac2033d644            Val   

                                          key                     key_final  \
27  3CG0019090_r01c04f01p01-ch2sk1fk1fl1.tiff  3CG0019090_r01c04f01p01.tiff   
31  3CG0019090_r01c04f05p01-ch2sk1fk1fl1.tiff  3CG0019090_r01c04f05p01.tiff   
32  3CG0019090_r01c04f06p01-ch2sk1fk1fl1.tiff  3CG0019090_r01c04f06p01.tiff   
34  3CG0019090_r01c04f08p01-ch2sk1fk1fl1.tiff  3CG0019090_r01c04f08p01.tiff   
36  3CG0019090_r01c05f01p01-ch2sk1fk1fl1.tiff  3CG0019090_r01c05f01p01.tiff   

    toxic  
27      0  
31      0  
32      0  
34      0  
36      0  

[5 rows x 34 columns]

In [ ]:
 train.iloc[0,1]

### Hack to get the original paths for lung 30k samples


In [8]:
def strings(python,input_file,output_file):
    return f'python {python} --input_file {input_file} --output_file {output_file}'

splits = [
    "train", "val", 
          "test"]

output_path = os.path.join(
    '/hpc/scratch/hdd3/smt29021/Tesaro-DNA-Damage/Data',
    'Breast/Step1_Preprocessing/ACT1_Normalise',
    'bf_fitc_30k_nontoxic/'
)
for split in splits:
    create_directory(os.path.join(output_path,split+"_A"))
    create_directory(os.path.join(output_path,split+"_B"))

train = lung_val_sig.iloc[:21000,[3,-2]]
print(f'Train Length {train.shape[0]}')
val = lung_val_sig.iloc[21000:27000,[3,-2]]
print(f'Val Length {val.shape[0]}')
test = lung_val_sig.iloc[27000:,[3,-2]]
print(f'Test Length {test.shape[0]}')
print(test.iloc[0,:])
command_list =[]
for index, tr in enumerate(train.iloc[:,0]):
    input_path_A = tr
    target_path_A = os.path.join(output_path, 'train_A',train.iloc[index,-1])
    command = strings(py_path, input_path_A, target_path_A)
    command_list.append(command)
    
    input_path_B = train.iloc[index,0][:-15]+"3"+train.iloc[index,0][-14:]
    target_path_B = os.path.join(output_path, 'train_B',train.iloc[index,-1])
    command = strings(py_path, input_path_B, target_path_B)
    command_list.append(command)
    
for index, tr in enumerate(val.iloc[:,0]):
    input_path_A = tr
    target_path_A = os.path.join(output_path, 'val_A',val.iloc[index,-1])
    command = strings(py_path, input_path_A, target_path_A)
    command_list.append(command)
    

    input_path_B = val.iloc[index,0][:-15]+"3"+val.iloc[index,0][-14:]
    target_path_B = os.path.join(output_path, 'val_B',val.iloc[index,-1])
    command = strings(py_path, input_path_B, target_path_B)
    command_list.append(command)
    
for index, tr in enumerate(test.iloc[:,0]):
    input_path_A = tr
    target_path_A = os.path.join(output_path, 'test_A',test.iloc[index,-1])
    command = strings(py_path, input_path_A, target_path_A)
    command_list.append(command)
    
    input_path_B = test.iloc[index,0][:-15]+"4"+test.iloc[index,0][-14:]
    target_path_B = os.path.join(output_path, 'test_B',test.iloc[index,-1])
    command = strings(py_path, input_path_B, target_path_B)
    command_list.append(command)
print(f'Total Commands {len(command_list)}')
command_list[:2]

Train Length 21000
Val Length 6000
Test Length 3000
image_url    /hpc/projects/upt/bioimaging_analytics/Tesaro-...
key_final                         3CG0019172_r09c16f09p01.tiff
Name: 144262, dtype: object
Total Commands 60000


['python /hpc/scratch/nvme3/smt29021/phase1_repo_1122/Structure-Specific-Contrast-Enhancement/workflow/phase2_sampling_normalisation/move_tesaro.py --input_file /hpc/projects/upt/bioimaging_analytics/Tesaro-DNA-Damage/2020-09/ELN15196_Br_DNA_Damage_Val_072220/ELN15196_Br_DNA_Damage_Val_data/ELN01154_72h_Br_DNA_Val/3CG0019090__2020-07-24T03_47_13-Measurement2/Images/r01c04f01p01-ch2sk1fk1fl1.tiff --output_file /hpc/scratch/hdd3/smt29021/Tesaro-DNA-Damage/Data/Breast/Step1_Preprocessing/ACT1_Normalise/bf_fitc_30k_nontoxic/train_A/3CG0019090_r01c04f01p01.tiff',
 'python /hpc/scratch/nvme3/smt29021/phase1_repo_1122/Structure-Specific-Contrast-Enhancement/workflow/phase2_sampling_normalisation/move_tesaro.py --input_file /hpc/projects/upt/bioimaging_analytics/Tesaro-DNA-Damage/2020-09/ELN15196_Br_DNA_Damage_Val_072220/ELN15196_Br_DNA_Damage_Val_data/ELN01154_72h_Br_DNA_Val/3CG0019090__2020-07-24T03_47_13-Measurement2/Images/r01c04f01p01-ch3sk1fk1fl1.tiff --output_file /hpc/scratch/hdd3/smt2

In [15]:
train_A = find_file(output_path+'/train_A/', ".tiff")
train_B = find_file(output_path+'/train_B/', ".tiff")
val_A = find_file(output_path+'/val_A/', ".tiff")
val_B = find_file(output_path+'/val_B/', ".tiff")
test_A = find_file(output_path+'/test_A/', ".tiff")
test_B = find_file(output_path+'/test_B/', ".tiff")
print(f'Total train_A: {len(train_A)}\nTotal train_B: {len(train_B)}\nTotal val_A: {len(val_A)}\nTotal val_B: {len(val_B)}\nTotal test_A: {len(test_A)}\nTotal test_B: {len(test_B)}\n')



Total train_A: 0
Total train_B: 0
Total val_A: 0
Total val_B: 0
Total test_A: 0
Total test_B: 0



### Generate folders, slurm command and run job

In [2]:
import os
import pandas as pd
from tifffile import imsave, imread

In [19]:
paths.iloc[row,col][:-15]+str(t)+paths.iloc[row,col][-14:]

'/hpc/projects/upt/bioimaging_analytics/Tesaro-DNA-Damage/2020-09/ELN15212_Lu_Ov__DNA_Damage_Val_091020/ELN15212_Lu_Ov_DNA_Damage_Val_Data/Lung/3CG0021748__2020-09-12T10_26_23-Measurement1/Images/r04c04f08p01-ch4sk1fk1fl1.tiff'

In [39]:
_30000_bf.iloc[21000,1]

'/hpc/projects/upt/bioimaging_analytics/Tesaro-DNA-Damage/2020-09/ELN15212_Lu_Ov__DNA_Damage_Val_091020/ELN15212_Lu_Ov_DNA_Damage_Val_Data/Lung/3CG0021748__2020-09-12T10_26_23-Measurement1/Images/r12c20f09p01-ch2sk1fk1fl1.tiff'

In [16]:
_30000_bf.head(1)

Unnamed: 0                                          image_url  \
12850       12850  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   

                                                new_path  \
12850  3CG0021772_r15c21f09p01.tiffTesaro-DNA-Damage-...   

                                                 new_loc  
12850  /hpc/projects/upt/bioimaging_analytics/Tesaro-...

In [19]:
## Manual method
## Non-mandatory to update
repo_path = os.path.join('/hpc/projects/upt/samuel_tonks_experimental_space/repos/gskgithub/virtual_staining/workflow/phase2_sampling_normalisation/')
py_path = os.path.join(repo_path,
                       'move_tesaro.py'
)

csv_path = os.path.join(
    '/hpc/projects/upt/bioimaging_analytics/Tesaro-DNA-Damage/images_and_metadata.csv'
)

random_val_samples_path = os.path.join(
    "/hpc/scratch/rdip1/smt29021/Tesaro-DNA-Damage/Data/DATA_Processing/"
)

good_lung_val_csv_path = os.path.join(
    '/hpc/projects/upt/bioimaging_analytics/Tesaro-DNA-Damage/error_analysis/lung_val_good_bf.csv',
#     'lu_val_good_bf.csv'
)


### Retrospective move of bf_dna_16bit_lung_val2_30000imgs which are cropped to 1056 1056 need to be 1080.


#Import Tesaro CSV
full_dataset = pd.read_csv(csv_path)
print("Number of Images: "+str(full_dataset.shape[0]))
full_dataset.head()

### Toxic/Non-toxic sampling

img_data = pd.read_csv(good_lung_val_csv_path)
# img_data = img_data.loc[img_data['toxic']==0]
# print("Number of Images: "+str(img_data.shape[0]))
img_data.head()
#

 
### Load txt file containing row index of chosen Bright-field samples and then generate the corresponding target paths

'/hpc/scratch/rdip1/smt29021/Tesaro-DNA-Damage/Data/DATA_Processing/'
#Generate bf samples
indexes, _30000_bf = extract_samples("lu_val_toxicsamples_30000.txt",img_data,random_val_samples_path)
tissue = 'Lung'
# _30000_bf = _30000_bf.iloc[:,0]
# _30000_bf.columns
# _30000_bf.iloc[0,-6]
_30000_bf.head()





Number of Images: 2562351


Unnamed: 0                           AbsTime AcquisitionType  \
18147       18147  2020-09-12 08:10:32.293000-04:00  NipkowConfocal   
16099       16099  2020-09-10 22:08:29.033000-04:00  NipkowConfocal   
8343         8343  2020-09-11 23:40:12.287000-04:00  NipkowConfocal   
16024       16024  2020-09-10 21:46:27.303000-04:00  NipkowConfocal   
18036       18036  2020-09-12 08:43:33.467000-04:00  NipkowConfocal   

         CameraType  ChannelID  ChannelName  Col  \
18147  AndorZylaCam          2  Brightfield    1   
16099  AndorZylaCam          2  Brightfield   14   
8343   AndorZylaCam          2  Brightfield   16   
16024  AndorZylaCam          2  Brightfield    6   
18036  AndorZylaCam          2  Brightfield   13   

                                            ExposureTime  FieldID  \
18147  [[0.987911,0,0,-21.6],[0,-0.987911,0,16.5],[0,...        9   
16099  [[0.987911,0,0,-21.6],[0,-0.987911,0,16.5],[0,...        4   
8343   [[0.987911,0,0,-21.6],[0,-0.987911,0,16.5],[0,...        6   
16024  [[0.987911,0,0,-21.6],[0,-0.987911,0,16.5],[0,...        1   
18036  [[0.987911,0,0,-21.6],[0,-0.987911,0,16.5],[0,...        6   

      IlluminationType  ...  Unnamed: 0.1.1.1.1  Unnamed: 0.1.1.1.1.1  \
18147      Transmitted  ...             18147.0               18147.0   
16099      Transmitted  ...             16099.0               16099.0   
8343       Transmitted  ...              8343.0                8343.0   
16024      Transmitted  ...             16024.0               16024.0   
18036      Transmitted  ...             18036.0               18036.0   

       final_cell_line                          image_folder1  \
18147       3CG0021732  ELN15212_Lu_Ov__DNA_Damage_Val_091020   
16099       3CG0021760  ELN15212_Lu_Ov__DNA_Damage_Val_091020   
8343        3CG0021770  ELN15212_Lu_Ov__DNA_Damage_Val_091020   
16024       3CG0021760  ELN15212_Lu_Ov__DNA_Damage_Val_091020   
18036       3CG0021732  ELN15212_Lu_Ov__DNA_Damage_Val_091020   

                                               image_url  \
18147  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   
16099  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   
8343   /hpc/projects/upt/bioimaging_analytics/Tesaro-...   
16024  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   
18036  /hpc/projects/upt/bioimaging_analytics/Tesaro-...   

                                             key  \
18147  3CG0021732_r05c01f09p01-ch2sk1fk1fl1.tiff   
16099  3CG0021760_r11c14f04p01-ch2sk1fk1fl1.tiff   
8343   3CG0021770_r07c16f06p01-ch2sk1fk1fl1.tiff   
16024  3CG0021760_r11c06f01p01-ch2sk1fk1fl1.tiff   
18036  3CG0021732_r04c13f06p01-ch2sk1fk1fl1.tiff   

                          key_final  plate_setting  tissue_final  toxic  
18147  3CG0021732_r05c01f09p01.tiff            Val          Lung      0  
16099  3CG0021760_r11c14f04p01.tiff            Val          Lung      0  
8343   3CG0021770_r07c16f06p01.tiff            Val          Lung      0  
16024  3CG0021760_r11c06f01p01.tiff            Val          Lung      0  
18036  3CG0021732_r04c13f06p01.tiff            Val          Lung      1  

[5 rows x 35 columns]

In [18]:
img_data.shape

(2364600, 4)

In [20]:
dapi_new_path= os.path.join(f'/hpc/projects/upt/samuel_tonks_experimental_space/datasets/Tesaro-DNA-Damage/Data/{tissue}/Step1_Preprocessing/ACT1_Normalise/bf_dna_30k_toxic/')
fitc_new_path= os.path.join(f'/hpc/projects/upt/samuel_tonks_experimental_space/datasets/Tesaro-DNA-Damage/Data/{tissue}/Step1_Preprocessing/ACT1_Normalise/bf_fitc_30k_toxic/')
cy5_new_path = os.path.join(f'/hpc/projects/upt/samuel_tonks_experimental_space/datasets/Tesaro-DNA-Damage/Data/{tissue}/Step1_Preprocessing/ACT1_Normalise/bf_cy5_30k_toxic/')

create_directory(dapi_new_path)
create_directory(fitc_new_path)
create_directory(cy5_new_path)
for i in ['train','val']:
    create_directory(os.path.join(dapi_new_path,i+'_A'))
    create_directory(os.path.join(dapi_new_path,i+'_B'))
    create_directory(os.path.join(fitc_new_path,i+'_A'))
    create_directory(os.path.join(fitc_new_path,i+'_B'))
    create_directory(os.path.join(cy5_new_path,i+'_A'))
    create_directory(os.path.join(cy5_new_path,i+'_B'))

train_30000_bf = _30000_bf.iloc[:21000,:]
val_30000_bf = _30000_bf.iloc[21000:27000,:]


Successfully create the directory /hpc/projects/upt/samuel_tonks_experimental_space/datasets/Tesaro-DNA-Damage/Data/Lung/Step1_Preprocessing/ACT1_Normalise/bf_dna_30k_toxic/
Successfully create the directory /hpc/projects/upt/samuel_tonks_experimental_space/datasets/Tesaro-DNA-Damage/Data/Lung/Step1_Preprocessing/ACT1_Normalise/bf_fitc_30k_toxic/
Successfully create the directory /hpc/projects/upt/samuel_tonks_experimental_space/datasets/Tesaro-DNA-Damage/Data/Lung/Step1_Preprocessing/ACT1_Normalise/bf_cy5_30k_toxic/
Successfully create the directory /hpc/projects/upt/samuel_tonks_experimental_space/datasets/Tesaro-DNA-Damage/Data/Lung/Step1_Preprocessing/ACT1_Normalise/bf_dna_30k_toxic/train_A
Successfully create the directory /hpc/projects/upt/samuel_tonks_experimental_space/datasets/Tesaro-DNA-Damage/Data/Lung/Step1_Preprocessing/ACT1_Normalise/bf_dna_30k_toxic/train_B
Successfully create the directory /hpc/projects/upt/samuel_tonks_experimental_space/datasets/Tesaro-DNA-Damage/Data

'r15c24f09p01_input.tiff'

In [22]:

# # #Generate target channels and inputs for move
# _val_4ch = channel_create(_30000_bf,0)
# _val_sig = image_folder_match(full_dataset,_30000_bf,"image_url","Brightfield")

# Generate targets 
target_path_old = []
target_path_new = []
source_path_new = []
source_path_old = []
paths = train_30000_bf
print(f'Total Train {paths.shape[0]}')
col = -6
for row in range(paths.shape[0]):
    
    for t in [1,3,4]:
        if t ==1:
            # BF path
            source_path_old.append(paths.iloc[row,col])
            # Save BF in new loc with new name
            source_path_new.append(os.path.join(dapi_new_path,'train_A',paths.iloc[row,col].split('/')[-3][:11])+paths.iloc[row,col].split('/')[-1][:12]+'_input.tiff')
            # Stain path
            target_path_old.append(paths.iloc[row,col][:-15]+str(t)+paths.iloc[row,col][-14:])
            target_path_new.append(os.path.join(dapi_new_path,'train_B',paths.iloc[row,col].split('/')[-3][:11])+paths.iloc[row,col].split('/')[-1][:12]+'_real.tiff')
        if t ==3:
            source_path_old.append(paths.iloc[row,col])
            source_path_new.append(os.path.join(fitc_new_path,'train_A',paths.iloc[row,col].split('/')[-3][:11])+paths.iloc[row,col].split('/')[-1][:12]+'_input.tiff')
            target_path_old.append(paths.iloc[row,col][:-15]+str(t)+paths.iloc[row,col][-14:])
            target_path_new.append(os.path.join(fitc_new_path,'train_B',paths.iloc[row,col].split('/')[-3][:11])+paths.iloc[row,col].split('/')[-1][:12]+'_real.tiff')
        if t ==4:
            source_path_old.append(paths.iloc[row,col])
            source_path_new.append(os.path.join(cy5_new_path,'train_A',paths.iloc[row,col].split('/')[-3][:11])+paths.iloc[row,col].split('/')[-1][:12]+'_input.tiff')
            target_path_old.append(paths.iloc[row,col][:-15]+str(t)+paths.iloc[row,col][-14:])
            target_path_new.append(os.path.join(cy5_new_path,'train_B',paths.iloc[row,col].split('/')[-3][:11])+paths.iloc[row,col].split('/')[-1][:12]+'_real.tiff')
        else:
            continue
print(len(target_path_old))
print(len(target_path_new))
paths = val_30000_bf      
print(f'Total Val {paths.shape[0]}')
for row in range(paths.shape[0]):
    for t in [1,3,4]:
        if t ==1:
            
            source_path_old.append(paths.iloc[row,col])
            source_path_new.append(os.path.join(dapi_new_path,'val_A',paths.iloc[row,col].split('/')[-3][:11])+paths.iloc[row,col].split('/')[-1][:12]+'_input.tiff')
            target_path_old.append(paths.iloc[row,col][:-15]+str(t)+paths.iloc[row,col][-14:])
            target_path_new.append(os.path.join(dapi_new_path,'val_B',paths.iloc[row,col].split('/')[-3][:11])+paths.iloc[row,col].split('/')[-1][:12]+'.tiff')
        if t ==3:
            
            source_path_old.append(paths.iloc[row,col])
            source_path_new.append(os.path.join(fitc_new_path,'val_A',paths.iloc[row,col].split('/')[-3][:11])+paths.iloc[row,col].split('/')[-1][:12]+'_input.tiff')
            target_path_old.append(paths.iloc[row,col][:-15]+str(t)+paths.iloc[row,col][-14:])
            target_path_new.append(os.path.join(fitc_new_path,'val_B',paths.iloc[row,col].split('/')[-3][:11])+paths.iloc[row,col].split('/')[-1][:12]+'_real.tiff')
        if t ==4:
            
            source_path_old.append(paths.iloc[row,col])
            source_path_new.append(os.path.join(cy5_new_path,'val_A',paths.iloc[row,col].split('/')[-3][:11])+paths.iloc[row,col].split('/')[-1][:12]+'_input.tiff')
            target_path_old.append(paths.iloc[row,col][:-15]+str(t)+paths.iloc[row,col][-14:])
            target_path_new.append(os.path.join(cy5_new_path,'val_B',paths.iloc[row,col].split('/')[-3][:11])+paths.iloc[row,col].split('/')[-1][:12]+'_real.tiff')
        else:
            continue
# paths = test_30000_bf
# print(f'Total Test {paths.shape[0]}')

# for row in range(paths.shape[0]):
#     for t in [1,3,4]:
#         if t ==1:
            
#             source_path_old.append(paths.iloc[row,0])
#             source_path_new.append(os.path.join(dapi_new_path,'test_A',paths.iloc[row,-2]))
#             target_path_old.append(paths.iloc[row,0][:-15]+str(t)+paths.iloc[row,0][-14:])
#             target_path_new.append(os.path.join(dapi_new_path,'test_B',paths.iloc[row,-2]))
#         if t ==3:
            
#             source_path_old.append(paths.iloc[row,0])
#             source_path_new.append(os.path.join(fitc_new_path,'test_A',paths.iloc[row,-2]))
#             target_path_old.append(paths.iloc[row,0][:-15]+str(t)+paths.iloc[row,0][-14:])
#             target_path_new.append(os.path.join(fitc_new_path,'test_B',paths.iloc[row,-2]))
#         if t ==4:
            
#             source_path_old.append(paths.iloc[row,0])
#             source_path_new.append(os.path.join(cy5_new_path,'test_A',paths.iloc[row,-2]))
#             target_path_old.append(paths.iloc[row,0][:-15]+str(t)+paths.iloc[row,0][-14:])
#             target_path_new.append(os.path.join(cy5_new_path,'test_B',paths.iloc[row,-2]))
#         else:
#             continue

print(len(target_path_old))
print(len(target_path_new))
print(source_path_old[0],source_path_new[0])

print(source_path_old[100],source_path_new[100])




Total Train 21000
63000
63000
Total Val 6000
81000
81000
/hpc/projects/upt/bioimaging_analytics/Tesaro-DNA-Damage/2020-09/ELN15212_Lu_Ov__DNA_Damage_Val_091020/ELN15212_Lu_Ov_DNA_Damage_Val_Data/Lung/3CG0021732__2020-09-12T08_08_20-Measurement1/Images/r05c01f09p01-ch2sk1fk1fl1.tiff /hpc/projects/upt/samuel_tonks_experimental_space/datasets/Tesaro-DNA-Damage/Data/Lung/Step1_Preprocessing/ACT1_Normalise/bf_dna_30k_toxic/train_A/3CG0021732_r05c01f09p01_input.tiff
/hpc/projects/upt/bioimaging_analytics/Tesaro-DNA-Damage/2020-09/ELN15212_Lu_Ov__DNA_Damage_Val_091020/ELN15212_Lu_Ov_DNA_Damage_Val_Data/Lung/3CG0021814__2020-09-11T01_08_44-Measurement1/Images/r06c04f04p01-ch2sk1fk1fl1.tiff /hpc/projects/upt/samuel_tonks_experimental_space/datasets/Tesaro-DNA-Damage/Data/Lung/Step1_Preprocessing/ACT1_Normalise/bf_fitc_30k_toxic/train_A/3CG0021814_r06c04f04p01_input.tiff


In [23]:
print(target_path_old[30000], target_path_new[30000])

/hpc/projects/upt/bioimaging_analytics/Tesaro-DNA-Damage/2020-09/ELN15212_Lu_Ov__DNA_Damage_Val_091020/ELN15212_Lu_Ov_DNA_Damage_Val_Data/Lung/3CG0021770__2020-09-11T22_57_28-Measurement1/Images/r03c12f01p01-ch1sk1fk1fl1.tiff /hpc/projects/upt/samuel_tonks_experimental_space/datasets/Tesaro-DNA-Damage/Data/Lung/Step1_Preprocessing/ACT1_Normalise/bf_dna_30k_toxic/train_B/3CG0021770_r03c12f01p01_real.tiff


In [24]:
for j in tqdm(range(len(source_path_old))):
    source = imread(source_path_old[j])
    imsave(source_path_new[j],source.astype(np.float32),imagej=True)
    target = imread(target_path_old[j])
    imsave(target_path_new[j],target.astype(np.float32),imagej=True)


  0%|          | 309/81000 [01:12<4:23:10,  5.11it/s]


  1%|          | 620/81000 [02:32<4:02:47,  5.52it/s]


  1%|          | 940/81000 [03:49<6:04:19,  3.66it/s]


  2%|▏         | 1256/81000 [05:08<3:34:48,  6.19it/s]


  2%|▏         | 1563/81000 [06:22<6:10:30,  3.57it/s]


...

 99%|█████████▊| 79885/81000 [5:14:22<04:41,  3.96it/s]


 99%|█████████▉| 80212/81000 [5:15:27<02:26,  5.39it/s]


 99%|█████████▉| 80522/81000 [5:16:31<01:39,  4.80it/s]


100%|█████████▉| 80832/81000 [5:17:35<00:29,  5.74it/s]


100%|██████████| 81000/81000 [5:18:08<00:00,  4.24it/s]

### End